In [16]:
from netgen.occ import *
from ngsolve import *
from ngsolve.webgui import Draw
import ngsolve as ngs
import netgen.occ as ngocc

import matplotlib.pyplot as plt
import numpy as np

In [17]:
wp = WorkPlane()


dom0 = wp.Direction(0,1).Line(2, "dirichlet").Line(9).Line(2, "dirichlet").LineTo(15,8).Direction(0,-1).Line(3, "neumann").LineTo(0,0).Close().Reverse().Face()

dom1 = wp.Circle(2.85,6.5,0.8).Face()
dom2 = wp.Circle(7.3,6.5,0.8).Face()
dom3 = wp.Circle(11.75,6.5,0.8).Face()

dom4 = wp.Circle(5.1625,8.5,0.8).Face()
dom5 = wp.Circle(9.6125,8.5,0.8).Face()

dom6 = wp.Circle(5.1625,4.5,0.8).Face()
dom7 = wp.Circle(9.6125,4.5,0.8).Face()

geo = dom0-dom1-dom2-dom3-dom4-dom5-dom6-dom7
Draw(geo)

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'ngsolve_version': 'Netgen x.x', 'mesh_dim': 3…

BaseWebGuiScene

In [18]:
shape = ngocc.OCCGeometry(geo, dim=2)
mesh = Mesh(shape.GenerateMesh(maxh=0.3))
Draw(mesh)

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

BaseWebGuiScene

We want to solve the unconstrained shape optimization problem
$$
            \underset{\Omega}{\mbox{min}} \;J(\Omega) + l Vol(\Omega) = \int_\Omega \sigma(u_\Omega):\epsilon(u_\Omega) \; dx + l  \int_\Omega 1 \:dx
$$
where $u_\Omega$ is the solution to the linear elasticity pde.

In [19]:
#Linear elasticity
E, nu = 1, 0.3  # Young's modulus und Poisson's ratio (Rubber)
mu = E / 2 / (1+nu) # Shear modulus
lam = E * nu / ((1+nu)*(1-2*nu)) # lame constant

eps = lambda u: 0.5 * (Grad(u) + Grad(u).trans)  # strain-rate tensor
sigma = lambda u: lam * Trace(eps(u)) * Id(2) + 2 * mu * eps(u)  # stress tensor

In [20]:
l=12
def Cost(u, v):
    compliance = InnerProduct(sigma(u), eps(v))*dx
    volume = CoefficientFunction(1) * dx
    return compliance + volume

In [21]:
fes = VectorH1(mesh, order=2, dirichlet = "dirichlet")

In [22]:
def SolveStateEquation():
    u, v = fes.TnT()
    a = BilinearForm(fes)
    a += InnerProduct(sigma(u), eps(v)) * dx
    a.Assemble()
    ainv = a.mat.Inverse(fes.FreeDofs())
    
    g = ngs.CF((0,-1))
    f = LinearForm(fes)
    f+= g * v * ds("neumann")
    f.Assemble()
    
    gfu = GridFunction(fes)
    gfu.vec.data = ainv * f.vec

    p, w = fes.TnT()

    
    rhs_adjoint = LinearForm(fes)
    rhs_adjoint += (-1) * Cost(gfu, gfu).Diff(gfu, w)
    rhs_adjoint.Assemble()
    gfp = GridFunction(fes)
    gfp.vec.data = ainv * rhs_adjoint.vec
    
    return gfu, gfp
gfu, gfp = SolveStateEquation()
Draw(gfu, mesh)
Draw(gfp, mesh)

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {}, 'ngsolve_version': '6.2.24…

BaseWebGuiScene

In [23]:
cost = Integrate(Cost(gfu, gfu), mesh)
print("Cost =", cost)

Cost = 349.9818829714488


In [24]:
def SolveDeformationEquation():
    g = ngs.CF((0,-1))
    Lagrangian = Cost(gfu, gfu) - InnerProduct(sigma(gfu), eps(gfu))*dx + g*gfu*ds("neumann")
    
    VEC = H1(mesh, order=2, dim=2, dirichlet="dirichlet")
    (PHI, X) = VEC.TnT()
    
    dJ_Omega = LinearForm(VEC)
    dJ_Omega += Lagrangian.DiffShape(X)
    
    # Shape Diff glätten
    my_mesh_size = 0.3
    b = BilinearForm(VEC)
    reg_param = 3*my_mesh_size**2
    b += reg_param * InnerProduct(grad(X), grad(PHI)) * dx + InnerProduct(X, PHI) * dx
    # add Cauchy-Riemann equation for better angle-preserving deformations
    alpha = 10
    b += alpha * (PHI.Deriv()[0,0] - PHI.Deriv()[1,1])*(X.Deriv()[0,0] - X.Deriv()[1,1]) *dx
    b += alpha * (PHI.Deriv()[1,0] + PHI.Deriv()[0,1])*(X.Deriv()[1,0] + X.Deriv()[0,1]) *dx
    
    gfX = GridFunction(VEC)
    b.Assemble()
    dJ_Omega.Assemble()
    rhs = gfX.vec.CreateVector()
    rhs.data = dJ_Omega.vec
    gfX.vec.data = b.mat.Inverse(VEC.FreeDofs()) * rhs

    return gfX
gfX = SolveDeformationEquation()

In [25]:
fesD = VectorH1(mesh, order=2)
gfset = GridFunction(fesD)
gfset.Set((0,0))

In [26]:
my_settings = {"colormap_ncolors" : 256, "line_thickness" : 3}
scene_X = Draw(-gfX, mesh, "-gfX", deformation=gfset, settings=my_settings)

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {'colormap_ncolors': 256, 'lin…

In [27]:
scene_u = Draw(gfu, mesh, "state", deformation=gfset, settings=my_settings)

WebGuiWidget(layout=Layout(height='50vh', width='100%'), value={'gui_settings': {'colormap_ncolors': 256, 'lin…

In [ ]:
do_this_block = True
if do_this_block:
    # Reset to zero deformation and solve for initial configuration
    gfset.Set((0,0))
    mesh.SetDeformation(gfset)
    gfu, gfp = SolveStateEquation()
    Jold = Integrate(Cost(gfu, gfu), mesh)
    vol = l * Integrate(CF(1), mesh)
    mesh.UnsetDeformation()

    # Settings for the gradient descent algorithm
    my_mesh_size = 0.3
    LineSearch = True
    max_backtrack = False
    curr_iter = 0
    TOL_func = 1e-12
    TOL_opt = 1e-12
    TOL_stepsize = 1e-15
    iter_max = 400

    print(' it  J             V          |dJ|       stepsize')
    print("%3d  %1.6e  %1.3e          -          -" % (curr_iter, Jold, vol))

    while curr_iter < iter_max:
        # Solve on current shape
        mesh.SetDeformation(gfset)  
        gfu, gfp = SolveStateEquation()
        gfX = SolveDeformationEquation()   

        # Compute descent direction in magnitude of mesh size
        scale = 0.1 * my_mesh_size / Norm(gfX.vec)
        gfsetOld = gfset.vec.CreateVector()
        gfsetOld.data = gfset.vec

        # Apply descent step
        gfset.vec.data -= scale * gfX.vec

        # Recompute state on new shape
        mesh.SetDeformation(gfset)
        gfu, gfp = SolveStateEquation()
        Jnew = Integrate(Cost(gfu, gfu), mesh)
        vol = l * Integrate(CF(1), mesh)
        mesh.UnsetDeformation()

        # Line search (Armijo)
        k_line_search = 1
        if LineSearch:
            while Jnew > Jold - 1e-4 * scale * Norm(gfX.vec)**2:
                scale = scale / 2
                k_line_search *= 0.5

                if k_line_search <= TOL_stepsize:
                    max_backtrack = True
                    break

                # revert and reapply scaled step
                gfset.vec.data = gfsetOld - scale * gfX.vec

                # update solution on new shape
                mesh.SetDeformation(gfset)
                gfu, gfp = SolveStateEquation()
                Jnew = Integrate(Cost(gfu, gfu), mesh)
                vol = l * Integrate(CF(1), mesh)
                mesh.UnsetDeformation()

        curr_iter += 1
        print("%3d  %1.6e  %1.3e  %1.3e  %1.3e" % (curr_iter, Jnew, vol, Norm(gfX.vec), k_line_search))

        if max_backtrack:
            print("Maximum iterations in line search reached. Algorithm may not have converged.")
            break

        # convergence criteria
        if abs(Jnew - Jold) < TOL_func:
            print("Converged to optimal shape (cost).")
            break
        if Norm(gfX.vec) < TOL_opt:
            print("Converged to optimal shape (gradient norm).")
            break

        Jold = Jnew
        scene_u.Redraw()
        scene_X.Redraw()

    if curr_iter == iter_max:
        print("Maximum number of iterations reached. Algorithm may not have converged!")


 it  J             V          |dJ|       stepsize
  0  3.499819e+02  1.275e+03          -          -
  1  3.499391e+02  1.275e+03  6.272e+02  1.000e+00
  2  3.498963e+02  1.275e+03  6.270e+02  1.000e+00
  3  3.498536e+02  1.275e+03  6.268e+02  1.000e+00
  4  3.498110e+02  1.275e+03  6.266e+02  1.000e+00
  5  3.497684e+02  1.275e+03  6.265e+02  1.000e+00
  6  3.497260e+02  1.275e+03  6.263e+02  1.000e+00
  7  3.496837e+02  1.275e+03  6.261e+02  1.000e+00
  8  3.496416e+02  1.275e+03  6.260e+02  1.000e+00
  9  3.495997e+02  1.275e+03  6.258e+02  1.000e+00
 10  3.495581e+02  1.275e+03  6.256e+02  1.000e+00
 11  3.495166e+02  1.275e+03  6.255e+02  1.000e+00
 12  3.494755e+02  1.276e+03  6.253e+02  1.000e+00
 13  3.494347e+02  1.276e+03  6.251e+02  1.000e+00
 14  3.493942e+02  1.276e+03  6.250e+02  1.000e+00
 15  3.493541e+02  1.276e+03  6.248e+02  1.000e+00
 16  3.493144e+02  1.276e+03  6.247e+02  1.000e+00
 17  3.492751e+02  1.276e+03  6.245e+02  1.000e+00
 18  3.492363e+02  1.276e+03  6.